In [2]:
import json
data1 = []
data2 = []
# with open( '../data/eth-registrar-decoded-3605331-to-5787413.json' ) as f:
#     for line in f:
#         data.append( json.loads( line ) )
with open( '../data/ens-3327417-to-5787413-decoded.json' ) as f:
    for line in f:
        data2.append( json.loads( line ) )
for rec in data2:
    rec[ 'blockNumberHuman' ] = int( rec[ 'blockNumber' ], 16 )

In [3]:
from collections import defaultdict

In [4]:
addresses = defaultdict( list )
for rec in data2:
    if 'owner' in rec[ 'args' ]:
        addresses[ rec[ 'args' ][ 'owner' ] ].append( rec )

In [6]:
from web3 import Web3

def hashname( node, label ):
    try:
        args = [ arg if '0x' != arg[ :2 ] else arg[ 2: ] for arg in [ node, label ] ]
        h = Web3.soliditySha3( [ 'bytes32' for _ in args ], tuple( bytes.fromhex( arg ) for arg in args ) )
    except Exception as e:
        print( args )
        raise
    return h.hex()


def new_owner( node, owner, label, block_no ):
    h = hashname( node, label )
    if h in nodes:
        previous_address = nodes[ h ].transfer( owner, block_no )
    else:
        nodes[ h ] = Node( h )
        previous_address = nodes[ h ].transfer( owner, block_no )
    addresses[ owner ].own( h, block_no )
    if previous_address is not None:
        addresses[ previous_address ].lose( h, block_no )
    

def transfer( node, owner, block_no ):
    h = node
    if h in nodes:
        previous_address = nodes[ h ].transfer( owner, block_no )
    else:
        nodes[ h ] = Node( h )
        previous_address = nodes[ h ].transfer( owner, block_no )
    addresses[ owner ].own( h, block_no )
    if previous_address is not None:
        addresses[ previous_address ].lose( h, block_no )
    
class Address:
    def __init__( self, address ):
        self.address = address
        self.history = []
        self.current_nodes = []

        
    def own( self, node_hash, block_no ):
        self.current_nodes.append( node_hash )
        self.history.append( ( block_no, self.current_nodes[ : ] ) )

        
    def lose( self, node_hash, block_no ):
        self.current_nodes = [ node for node in self.current_nodes if node != node_hash ]
        self.history.append( ( block_no, self.current_nodes[ : ] ) )
     

    def to_json( self ):
        return {
            'address': self.address,
            'history': self.history,
            'current_nodes': self.current_nodes
        }
        
        
class Node:
    def __init__( self, node_hash ):
        self.node_hash = node_hash
        self.current_address = None
        self.history = []
    
    
    def transfer( self, new_owner, block_no ):
        self.history.append( ( block_no, new_owner ) )
        previous_owner = self.current_address
        self.current_address = new_owner
        return previous_owner
        
    def to_json( self ):
        return {
            'hash': self.node_hash,
            'history': self.history,
            'current_address': self.current_address
        }
    
nodes = {}
addresses = { address: Address( address ) for address in set( [ x[ 'args' ][ 'owner' ] for x in data2 if 'owner' in x[ 'args' ] ] )}


In [7]:
for rec in sorted( data2, key = lambda rec: rec[ 'blockNumberHuman' ] ):
    if rec[ 'event' ] == 'NewOwner':
        new_owner( rec[ 'args' ][ 'node' ], rec[ 'args' ][ 'owner' ], rec[ 'args' ][ 'label' ], rec[ 'blockNumberHuman' ] )
    elif rec[ 'event' ] == 'Transfer':
        transfer( rec[ 'args' ][ 'node' ], rec[ 'args' ][ 'owner' ], rec[ 'blockNumberHuman' ] )

In [8]:
n = nodes[ list( nodes.keys() )[ 2] ]
print( n.node_hash )
a = addresses[ list( addresses.keys() )[ 0 ] ]
print( a.address )

0xa097f6721ce401e757d1223a763fef49b8b5f90bb18567ddb86fd205dff71d34
0x618b325c8532ccb5eeae21befb0a1711ac7f9897


In [9]:
n.history

[(3330226, '0x8472d6206f381ebf71a174b9de9e61b0e1962da4'),
 (3330259, '0x0000000000000000000000000000000000000000')]

In [10]:
a = addresses[ '0x8472d6206f381ebf71a174b9de9e61b0e1962da4' ]
a.history

[(3327421,
  ['0x0000000000000000000000000000000000000000000000000000000000000000']),
 (3330226,
  ['0x0000000000000000000000000000000000000000000000000000000000000000',
   '0xa097f6721ce401e757d1223a763fef49b8b5f90bb18567ddb86fd205dff71d34']),
 (3330259,
  ['0x0000000000000000000000000000000000000000000000000000000000000000']),
 (3342524, [])]

In [11]:
import pymongo

In [21]:
db = pymongo.MongoClient('mongodb://localhost').ens

In [22]:
db_addr = db.addresses
db_node = db.nodes

In [23]:
for i, ( _, node ) in enumerate( nodes.items() ):
    print( i / len( nodes ), '%')
    db_node.insert_one( node.to_json() )

0.0 %
5.663540392370078e-06 %
1.1327080784740156e-05 %
1.6990621177110236e-05 %
2.2654161569480312e-05 %
2.8317701961850392e-05 %
3.398124235422047e-05 %
3.964478274659055e-05 %
4.5308323138960625e-05 %
5.097186353133071e-05 %
5.6635403923700784e-05 %
6.229894431607086e-05 %
6.796248470844094e-05 %
7.362602510081101e-05 %
7.92895654931811e-05 %
8.495310588555118e-05 %
9.061664627792125e-05 %
9.628018667029133e-05 %
0.00010194372706266142 %
0.00010760726745503148 %
0.00011327080784740157 %
0.00011893434823977165 %
0.00012459788863214172 %
0.0001302614290245118 %
0.0001359249694168819 %
0.00014158850980925197 %
0.00014725205020162203 %
0.0001529155905939921 %
0.0001585791309863622 %
0.00016424267137873228 %
0.00016990621177110236 %
0.00017556975216347244 %
0.0001812332925558425 %
0.00018689683294821258 %
0.00019256037334058266 %
0.00019822391373295275 %
0.00020388745412532283 %
0.0002095509945176929 %
0.00021521453491006297 %
0.00022087807530243305 %
0.00022654161569480314 %
0.0002322051

0.00291105976167822 %
0.0029167233020705903 %
0.0029223868424629604 %
0.0029280503828553305 %
0.0029337139232477006 %
0.0029393774636400707 %
0.002945041004032441 %
0.002950704544424811 %
0.002956368084817181 %
0.002962031625209551 %
0.002967695165601921 %
0.002973358705994291 %
0.002979022246386661 %
0.002984685786779031 %
0.0029903493271714013 %
0.0029960128675637714 %
0.0030016764079561415 %
0.0030073399483485116 %
0.0030130034887408817 %
0.003018667029133252 %
0.003024330569525622 %
0.003029994109917992 %
0.003035657650310362 %
0.0030413211907027323 %
0.003046984731095102 %
0.003052648271487472 %
0.003058311811879842 %
0.0030639753522722123 %
0.0030696388926645824 %
0.0030753024330569525 %
0.0030809659734493226 %
0.0030866295138416927 %
0.003092293054234063 %
0.003097956594626433 %
0.003103620135018803 %
0.003109283675411173 %
0.0031149472158035433 %
0.0031206107561959134 %
0.003126274296588283 %
0.003131937836980653 %
0.0031376013773730233 %
0.0031432649177653934 %
0.0031489284581

0.006105296542974944 %
0.006110960083367314 %
0.006116623623759684 %
0.0061222871641520545 %
0.006127950704544425 %
0.006133614244936795 %
0.006139277785329165 %
0.006144941325721535 %
0.006150604866113905 %
0.006156268406506275 %
0.006161931946898645 %
0.006167595487291015 %
0.0061732590276833855 %
0.006178922568075756 %
0.006184586108468126 %
0.006190249648860496 %
0.006195913189252866 %
0.006201576729645236 %
0.006207240270037606 %
0.006212903810429976 %
0.006218567350822346 %
0.0062242308912147165 %
0.006229894431607087 %
0.006235557971999457 %
0.006241221512391827 %
0.006246885052784196 %
0.006252548593176566 %
0.006258212133568936 %
0.006263875673961306 %
0.0062695392143536765 %
0.006275202754746047 %
0.006280866295138417 %
0.006286529835530787 %
0.006292193375923157 %
0.006297856916315527 %
0.006303520456707897 %
0.006309183997100267 %
0.006314847537492637 %
0.0063205110778850075 %
0.006326174618277378 %
0.006331838158669748 %
0.006337501699062118 %
0.006343165239454488 %
0.0063

0.009203253137601378 %
0.009208916677993747 %
0.009214580218386118 %
0.009220243758778487 %
0.009225907299170858 %
0.009231570839563228 %
0.009237234379955599 %
0.009242897920347968 %
0.009248561460740337 %
0.009254225001132708 %
0.009259888541525077 %
0.009265552081917448 %
0.009271215622309818 %
0.009276879162702189 %
0.009282542703094558 %
0.009288206243486929 %
0.009293869783879298 %
0.009299533324271669 %
0.009305196864664038 %
0.00931086040505641 %
0.009316523945448778 %
0.00932218748584115 %
0.009327851026233519 %
0.00933351456662589 %
0.009339178107018259 %
0.00934484164741063 %
0.009350505187802999 %
0.00935616872819537 %
0.00936183226858774 %
0.00936749580898011 %
0.00937315934937248 %
0.00937882288976485 %
0.00938448643015722 %
0.00939014997054959 %
0.00939581351094196 %
0.009401477051334331 %
0.0094071405917267 %
0.00941280413211907 %
0.00941846767251144 %
0.00942413121290381 %
0.00942979475329618 %
0.00943545829368855 %
0.009441121834080921 %
0.00944678537447329 %
0.009452

0.012233247247519369 %
0.01223891078791174 %
0.012244574328304109 %
0.01225023786869648 %
0.01225590140908885 %
0.01226156494948122 %
0.01226722848987359 %
0.01227289203026596 %
0.01227855557065833 %
0.0122842191110507 %
0.01228988265144307 %
0.01229554619183544 %
0.01230120973222781 %
0.012306873272620181 %
0.01231253681301255 %
0.012318200353404921 %
0.01232386389379729 %
0.012329527434189662 %
0.01233519097458203 %
0.0123408545149744 %
0.012346518055366771 %
0.01235218159575914 %
0.012357845136151511 %
0.01236350867654388 %
0.012369172216936251 %
0.01237483575732862 %
0.012380499297720992 %
0.012386162838113361 %
0.012391826378505732 %
0.012397489918898101 %
0.012403153459290472 %
0.012408816999682841 %
0.012414480540075212 %
0.012420144080467582 %
0.012425807620859953 %
0.012431471161252322 %
0.012437134701644693 %
0.012442798242037062 %
0.012448461782429433 %
0.012454125322821802 %
0.012459788863214173 %
0.012465452403606542 %
0.012471115943998913 %
0.012476779484391283 %
0.012482

...

0.9865604186489058 %
0.9865660821892982 %
0.9865717457296905 %
0.9865774092700829 %
0.9865830728104753 %
0.9865887363508676 %
0.9865943998912601 %
0.9866000634316524 %
0.9866057269720447 %
0.9866113905124372 %
0.9866170540528295 %
0.9866227175932218 %
0.9866283811336143 %
0.9866340446740066 %
0.986639708214399 %
0.9866453717547914 %
0.9866510352951837 %
0.986656698835576 %
0.9866623623759685 %
0.9866680259163608 %
0.9866736894567532 %
0.9866793529971456 %
0.9866850165375379 %
0.9866906800779304 %
0.9866963436183227 %
0.986702007158715 %
0.9867076706991075 %
0.9867133342394998 %
0.9867189977798921 %
0.9867246613202846 %
0.9867303248606769 %
0.9867359884010692 %
0.9867416519414617 %
0.986747315481854 %
0.9867529790222463 %
0.9867586425626388 %
0.9867643061030311 %
0.9867699696434235 %
0.9867756331838159 %
0.9867812967242082 %
0.9867869602646006 %
0.986792623804993 %
0.9867982873453853 %
0.9868039508857778 %
0.9868096144261701 %
0.9868152779665624 %
0.9868209415069549 %
0.9868266050473472

0.989426170087445 %
0.9894318336278375 %
0.9894374971682298 %
0.9894431607086221 %
0.9894488242490146 %
0.9894544877894069 %
0.9894601513297993 %
0.9894658148701917 %
0.989471478410584 %
0.9894771419509764 %
0.9894828054913688 %
0.9894884690317611 %
0.9894941325721535 %
0.9894997961125459 %
0.9895054596529382 %
0.9895111231933306 %
0.989516786733723 %
0.9895224502741153 %
0.9895281138145077 %
0.9895337773549001 %
0.9895394408952924 %
0.9895451044356849 %
0.9895507679760772 %
0.9895564315164695 %
0.989562095056862 %
0.9895677585972543 %
0.9895734221376467 %
0.9895790856780391 %
0.9895847492184314 %
0.9895904127588238 %
0.9895960762992162 %
0.9896017398396085 %
0.9896074033800009 %
0.9896130669203933 %
0.9896187304607856 %
0.989624394001178 %
0.9896300575415704 %
0.9896357210819627 %
0.9896413846223552 %
0.9896470481627475 %
0.9896527117031398 %
0.9896583752435323 %
0.9896640387839246 %
0.989669702324317 %
0.9896753658647094 %
0.9896810294051017 %
0.989686692945494 %
0.9896923564858865 %

0.9925694350052104 %
0.9925750985456028 %
0.9925807620859952 %
0.9925864256263875 %
0.99259208916678 %
0.9925977527071723 %
0.9926034162475647 %
0.9926090797879571 %
0.9926147433283494 %
0.9926204068687418 %
0.9926260704091342 %
0.9926317339495265 %
0.9926373974899189 %
0.9926430610303113 %
0.9926487245707036 %
0.992654388111096 %
0.9926600516514884 %
0.9926657151918807 %
0.9926713787322731 %
0.9926770422726655 %
0.9926827058130578 %
0.9926883693534503 %
0.9926940328938426 %
0.992699696434235 %
0.9927053599746274 %
0.9927110235150197 %
0.992716687055412 %
0.9927223505958045 %
0.9927280141361968 %
0.9927336776765892 %
0.9927393412169816 %
0.9927450047573739 %
0.9927506682977663 %
0.9927563318381587 %
0.992761995378551 %
0.9927676589189434 %
0.9927733224593358 %
0.9927789859997281 %
0.9927846495401205 %
0.9927903130805129 %
0.9927959766209052 %
0.9928016401612977 %
0.99280730370169 %
0.9928129672420823 %
0.9928186307824748 %
0.9928242943228671 %
0.9928299578632594 %
0.9928356214036519 %


0.9956673915998369 %
0.9956730551402293 %
0.9956787186806216 %
0.995684382221014 %
0.9956900457614064 %
0.9956957093017987 %
0.9957013728421911 %
0.9957070363825835 %
0.9957126999229758 %
0.9957183634633682 %
0.9957240270037606 %
0.995729690544153 %
0.9957353540845453 %
0.9957410176249377 %
0.99574668116533 %
0.9957523447057225 %
0.9957580082461148 %
0.9957636717865072 %
0.9957693353268996 %
0.9957749988672919 %
0.9957806624076843 %
0.9957863259480767 %
0.995791989488469 %
0.9957976530288614 %
0.9958033165692538 %
0.9958089801096461 %
0.9958146436500385 %
0.9958203071904309 %
0.9958259707308232 %
0.9958316342712156 %
0.995837297811608 %
0.9958429613520003 %
0.9958486248923928 %
0.9958542884327851 %
0.9958599519731774 %
0.9958656155135699 %
0.9958712790539622 %
0.9958769425943546 %
0.995882606134747 %
0.9958882696751393 %
0.9958939332155317 %
0.9958995967559241 %
0.9959052602963164 %
0.9959109238367088 %
0.9959165873771012 %
0.9959222509174935 %
0.9959279144578859 %
0.9959335779982783 %

0.998759684654071 %
0.9987653481944633 %
0.9987710117348557 %
0.998776675275248 %
0.9987823388156404 %
0.9987880023560328 %
0.9987936658964252 %
0.9987993294368176 %
0.9988049929772099 %
0.9988106565176023 %
0.9988163200579947 %
0.998821983598387 %
0.9988276471387794 %
0.9988333106791718 %
0.9988389742195641 %
0.9988446377599565 %
0.9988503013003489 %
0.9988559648407412 %
0.9988616283811336 %
0.998867291921526 %
0.9988729554619183 %
0.9988786190023107 %
0.9988842825427031 %
0.9988899460830954 %
0.9988956096234879 %
0.9989012731638802 %
0.9989069367042726 %
0.998912600244665 %
0.9989182637850573 %
0.9989239273254497 %
0.9989295908658421 %
0.9989352544062344 %
0.9989409179466268 %
0.9989465814870192 %
0.9989522450274115 %
0.9989579085678039 %
0.9989635721081963 %
0.9989692356485886 %
0.998974899188981 %
0.9989805627293734 %
0.9989862262697657 %
0.9989918898101581 %
0.9989975533505505 %
0.9990032168909428 %
0.9990088804313353 %
0.9990145439717276 %
0.99902020751212 %
0.9990258710525124 %


In [ ]:
for i, (_, address ) in enumerate( addresses.items() ):
    try:
        db_addr.insert_one( address.to_json() )
    except:
        pass
    if i % 1000 == 0:
        print( 100 * ( i / len( addresses ) ), '%' )

0.0 %
4.797313504437515 %
9.59462700887503 %
14.391940513312546 %
19.18925401775006 %
23.986567522187574 %
